In [1]:
import os
from dotenv import load_dotenv
import pandas as pd
import ontology_mapper_new

In [2]:
pd.options.display.max_rows = None  # display all rows
pd.options.display.max_columns = None  # display all columns
pd.set_option('display.max_colwidth', None) # don't truncate wide columns

In [3]:
load_dotenv()
API_KEY = os.getenv("BIOPORTAL_API_KEY")

In [4]:
ontology_mapper_new.map_ontology(API_KEY, ["inchi key"], topn=1000)

keyword pref_label      synonyms  \
0  inchi key  Inchi Key            ()   
1  inchi key  inchi key  (inchi key,)   

                                                                                                                                                                                                                                                                                                                                        definition  \
0                                                                                                                                                                                                                         (A condensed, fixed-length version of the InChI, designed to be a more accessible way of indexing chemical substances.,)   
1  (InChIKeys consist of 14 characters resulting from a hash of the connectivity information of the InChI, followed by a hyphen, followed by 9 characters resulting from a hash of the remaining layers of the InChI, followed by a single character indication the version of InChI used, another hyphen, followed by single checksum character,)   

                                  class  
0  https://purl.dsmz.de/schema/InchiKey  
1                               MI:0970

In [5]:
tier2 = pd.read_csv("../cdes/RADx-rad_tier2_dict_2024-08-22.csv", keep_default_na=False, dtype=str)

In [6]:
tier2.head()

Id  \
0             protocol_id   
1     technology_platform   
2  technology_description   
3    technology_reference   
4     biorecognition_type   

                                                                Label  \
0                    Unique name or identifier for biosensor protocol   
1                          Abbreviation or short label for technology   
2                                     Short description of technology   
3  URL of publication, preprint, or website that describes technology   
4             Type of molecular entity used for biosensor fabrication   

               Section Cardinality Terms Datatype Unit  \
0  Technology Metadata      single         string        
1  Technology Metadata      single         string        
2  Technology Metadata      single         string        
3  Technology Metadata      single         string        
4  Technology Metadata    multiple         string        

                                                                                                                                                                                                                                                                                                                 Enumeration  \
0                                                                                                                                                                                                                                                                                                                              
1                                                                                                                                                                                                                                                                                                                              
2                                                                                                                                                                                                                                                                                                                              
3                                                                                                                                                                                                                                                                                                                              
4  "aptamer"=[aptamer] | "antibody"=[antibody] | "antigen"=[antigen] | "molecular beacon"=[molecular beacon] | "nanobody"=[nanobody] | "primer"=[primer] | "receptor"=[receptor] | "DNA-oligonucleotide"=[DNA-oligonucleotide] | "analyte binding peptide"=[analyte binding peptide] | "enzyme-substrate"=[enzyme-substrate]   

                                                                                             Notes  \
0                                                                        example: ddPCR_SARS-CoV-2   
1                                                                                   example: ddPCR   
2                                                                     example: Droplet Digital PCR   
3                                                                                                    
4  Multiple entities can be specified as list if biosenor uses a combination of molecular entities   

                     MissingValueCodes    Provenance SeeAlso  
0  "-9960"=[Not Entered By Originator]  RADx-rad DCC          
1  "-9960"=[Not Entered By Originator]  RADx-rad DCC          
2  "-9960"=[Not Entered By Originator]  RADx-rad DCC          
3  "-9960"=[Not Entered By Originator]  RADx-rad DCC          
4  "-9960"=[Not Entered By Originator]  RADx-rad DCC

In [7]:
def split_string_variations(input_string):
    # Split the input string by underscores
    parts = input_string.split('_')
    
    # Store all possible substrings
    substrings = set()
    
    # Generate combinations of substrings by slicing the list of parts
    for i in range(len(parts)):
        for j in range(i + 1, len(parts) + 1):
            substrings.add(' '.join(parts[i:j]))  # Join with a space instead of underscore
    
    # Return the result as a list
    return sorted(substrings)

In [8]:
ids = tier2[["Id"]].copy()
ids["keyword"] = ids["Id"].apply(split_string_variations)
ids = ids.explode("keyword")
#ids = ids[1000:2000].copy()
print(f"Number of kewords: {ids.shape[0]}")
print(f"Number of unique keywords: {ids['keyword'].nunique()}")
keywords = list(ids["keyword"].unique())
ids.head()

Number of kewords: 7210
Number of unique keywords: 2411


Id      keyword
0          protocol_id           id
0          protocol_id     protocol
0          protocol_id  protocol id
1  technology_platform     platform
1  technology_platform   technology

In [9]:
ids.query("keyword == 'inchi key'")

Id    keyword
14   immobilization_reagent_inchi_key  inchi key
295               substrate_inchi_key  inchi key

In [12]:
chunks = ontology_mapper_new.create_chunks(keywords, 500)

for i, chunk in enumerate(chunks):
    if i < 3:
        continue
    print(f"chunk: {i}")
    mappings = ontology_mapper_new.map_ontology(API_KEY, chunk,topn=1000)
    mappings.fillna("", inplace=True)
    mappings.query("definition != ''", inplace=True)
    mappings = mappings[mappings['definition'] != ()]
    mappings.to_csv(f"ontology_mappings_{i}.csv", index=False)

chunk: 3
ERROR: Unable to fetch data (status code 404)
ERROR: Unable to fetch data (status code 404)
ERROR: Unable to fetch data (status code 404)
ERROR: Unable to fetch data (status code 404)
ERROR: Unable to fetch data (status code 404)
ERROR: Unable to fetch data (status code 404)
ERROR: Unable to fetch data (status code 404)
ERROR: Unable to fetch data (status code 404)
ERROR: Unable to fetch data (status code 404)
chunk: 4
ERROR: Unable to fetch data (status code 404)
ERROR: Unable to fetch data (status code 404)
ERROR: Unable to fetch data (status code 404)
ERROR: Unable to fetch data (status code 404)
ERROR: Unable to fetch data (status code 404)
ERROR: Unable to fetch data (status code 404)
ERROR: Unable to fetch data (status code 404)
ERROR: Unable to fetch data (status code 404)
ERROR: Unable to fetch data (status code 404)
ERROR: Unable to fetch data (status code 404)
ERROR: Unable to fetch data (status code 404)
ERROR: Unable to fetch data (status code 404)
ERROR: Unable to

In [15]:
#nchunks = len(list(chunks))
map_chunks = []
for i in range(5):
    print(i)
    df = pd.read_csv(f"ontology_mappings_{i}.csv", keep_default_na=False)
    map_chunks.append(df)

all_mappings = pd.concat(map_chunks)
all_mappings.drop_duplicates(inplace=True)
print(f"Number of mappings: {all_mappings.shape[0]}")
all_mappings.to_csv("ontology_mappings.csv", index=False)
all_mappings

0
1
2
3
4
Number of mappings: 1350


keyword  \
0                     protocol   
1                     protocol   
2                     protocol   
3                     protocol   
4                     protocol   
5                     protocol   
6                     platform   
7                     platform   
8                   technology   
9                   technology   
10                  technology   
11         technology platform   
12                 description   
13                 description   
14                 description   
15                 description   
16                   reference   
17                   reference   
18                   reference   
19                   reference   
20                   reference   
21                   reference   
22                        type   
23                        type   
24                        type   
25                     analyte   
26                     analyte   
27                     analyte   
28                     analyte   
29                analyte type   
30                      target   
31                      target   
32                      target   
33                analyte name   
34                   detection   
35                   detection   
36                   detection   
37                   detection   
38                   detection   
39                      signal   
40                      signal   
41                      signal   
42                     surface   
43                     surface   
44                 measurement   
45                 measurement   
46                 measurement   
47                 measurement   
48                 measurement   
49                 measurement   
50                 measurement   
51                 measurement   
52            measurement type   
53                  instrument   
54                  instrument   
55                  instrument   
56                  instrument   
57                  instrument   
58                  instrument   
59              immobilization   
60              immobilization   
61                     reagent   
62                     reagent   
63                     reagent   
64                     reagent   
65                     reagent   
66                     reagent   
67                reagent name   
68                       inchi   
69                       inchi   
70                       inchi   
71                         key   
72                         key   
73                         key   
74                         key   
75                      source   
76                      source   
77                      source   
78                      source   
79                      source   
80                   source id   
81                         url   
82                         url   
83                         url   
84                         url   
85      electrochemical method   
86                      method   
87                      method   
88                      method   
89                      method   
90                      method   
91                 method name   
92                    solution   
93                    solution   
94                    solution   
95                    solution   
96                    solution   
97                    solution   
98                    solution   
99                    solution   
100                  electrode   
101                  electrode   
102                  electrode   
103                  electrode   
104                  electrode   
105        reference electrode   
106        auxiliary electrode   
107                    working   
108          working electrode   
109                    aptamer   
110                    aptamer   
111                    aptamer   
112                    aptamer   
113                   sequence   
114                   sequence   
115                   sequence   
116                   sequence   
117        

In [14]:
#ontology_mapper_new.map_ontology(API_KEY, ["surface"], topn=100)